In [2]:
!pip install tqdm

  Using cached tqdm-4.67.1-py3-none-any.whl.metadata (57 kB)
Using cached tqdm-4.67.1-py3-none-any.whl (78 kB)


In [2]:
import os
import pandas as pd
import numpy as np
from scipy.integrate import solve_ivp
from collections import Counter
from tqdm import trange
import pprint
from IPython.display import display, Math

In [34]:

# 1) Load parameter names and parameter file
pt = "/Users/hiteshkandarpa/Desktop/IISC/Summer'25/Code/initial_sims/Toggle_tetrahedron/Hypothesis_test/"
params_file = os.path.join(pt, "TS_parameters.dat")
names_file  = os.path.join(pt, "TS.prs")

# Read TTr.txt, ignore first header line, take only first token of each subsequent line
with open(names_file, 'r') as f:
    lines = [ln.strip() for ln in f if ln.strip()]
param_names = [ln.split()[0] for ln in lines[1:]]

# Read the parameters: col0=S_no, col1=Reported_states, cols2+ = kinetic values
pars = pd.read_csv(
    params_file,
    delim_whitespace=True,
    header=None,
    names=["S_no", "Reported_states"] + param_names,
    nrows=100 
)

# Extract gene list ['A','B','C','D'] from "Prod_of_<Gene>"
genes = [nm.split("_")[-1] for nm in param_names if nm.startswith("Prod_of_")]

# 2) Euler integrator
def integrate_euler(f, X0, p, dt, n_steps):
    X = X0.copy()
    for _ in range(n_steps):
        dX = f(X, p)
        X += dt * dX
        X[X < 0] = 0
    return X

# 3) ODE RHS: Toggle-Tetrahedron with shifted-Hill kinetics
def ode_system(X, p):
    dX = np.zeros_like(X)
    for i, G in enumerate(genes):
        prod = p[f"Prod_of_{G}"]
        deg  = p[f"Deg_of_{G}"]
        for H in genes:
            if H == G:
                continue
            lam = p[f"Inh_of_{H}To{G}"]
            K   = p[f"Trd_of_{H}To{G}"]
            n   = p[f"Num_of_{H}To{G}"]
            print(f'Inh_of_{H}To{G} = {lam}, Trd_of_{H}To{G} = {K}, Num_of_{H}To{G} = {n}')
            Xj  = X[genes.index(H)]
            hill = Xj**n / (K**n + Xj**n)
            prod *= ((1 - lam) + lam * hill)
        dX[i] = prod - deg * X[i]
    return dX

# 4) Find unique steady states for one parameter set
def find_steady_states(param_row, n_ics=100, dt=0.1, n_steps=20000, tol_cluster=1.0):
    p = param_row[param_names].to_dict()
    finals = []
    for _ in range(n_ics):
        X0 = np.array([np.random.uniform(0, p[f"Prod_of_{G}"] / p[f"Deg_of_{G}"]) for G in genes])
        Xf = integrate_euler(ode_system, X0, p, dt, n_steps)
        if not any(np.allclose(Xf, F, atol=tol_cluster) for F in finals):
            finals.append(Xf)
    return finals

# 5) Simulate all parameter sets and write RACIPE-style output
output_file = os.path.join(pt, "simulated_steady_states.dat")
with open(output_file, 'w') as fout:
    for idx in trange(len(pars), desc="Simulating"):
        row = pars.iloc[idx]
        s_no = int(row["S_no"])
        ss   = find_steady_states(row)
        n_ss = len(ss)
        line = [s_no, n_ss] + [val for st in ss for val in st.tolist()]
        fout.write("\t".join(f"{v:.6g}" for v in line) + "\n")



/var/folders/6q/3gs9cqgs6ll9y2vljypxl7n80000gn/T/ipykernel_5232/3249076011.py:12: FutureWarning: The 'delim_whitespace' keyword in pd.read_csv is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  pars = pd.read_csv(
Simulating:   0%|          | 0/100 [00:00<?, ?it/s]

Inh_of_BToA = 0.086486, Trd_of_BToA = 0.180382, Num_of_BToA = 7.0
Inh_of_CToA = 0.058794, Trd_of_CToA = 0.028476, Num_of_CToA = 9.0
Inh_of_DToA = 0.023672, Trd_of_DToA = 0.715976, Num_of_DToA = 6.0
Inh_of_AToB = 0.035611, Trd_of_AToB = 0.908194, Num_of_AToB = 9.0
Inh_of_CToB = 0.038629, Trd_of_CToB = 0.242677, Num_of_CToB = 7.0
Inh_of_DToB = 0.077111, Trd_of_DToB = 0.452594, Num_of_DToB = 10.0
Inh_of_AToC = 0.012452, Trd_of_AToC = 0.074465, Num_of_AToC = 10.0
Inh_of_BToC = 0.013795, Trd_of_BToC = 1.201145, Num_of_BToC = 7.0
Inh_of_DToC = 0.015959, Trd_of_DToC = 0.457424, Num_of_DToC = 9.0
Inh_of_AToD = 0.011011, Trd_of_AToD = 0.246773, Num_of_AToD = 6.0
Inh_of_BToD = 0.010941, Trd_of_BToD = 1.061017, Num_of_BToD = 9.0
Inh_of_CToD = 0.088197, Trd_of_CToD = 1.212272, Num_of_CToD = 10.0
Inh_of_BToA = 0.086486, Trd_of_BToA = 0.180382, Num_of_BToA = 7.0
Inh_of_CToA = 0.058794, Trd_of_CToA = 0.028476, Num_of_CToA = 9.0
Inh_of_DToA = 0.023672, Trd_of_DToA = 0.715976, Num_of_DToA = 6.0
Inh_of_

Simulating:   0%|          | 0/100 [00:59<?, ?it/s]


Inh_of_BToD = 0.010941, Trd_of_BToD = 1.061017, Num_of_BToD = 9.0
Inh_of_CToD = 0.088197, Trd_of_CToD = 1.212272, Num_of_CToD = 10.0
Inh_of_BToA = 0.086486, Trd_of_BToA = 0.180382, Num_of_BToA = 7.0
Inh_of_CToA = 0.058794, Trd_of_CToA = 0.028476, Num_of_CToA = 9.0
Inh_of_DToA = 0.023672, Trd_of_DToA = 0.715976, Num_of_DToA = 6.0
Inh_of_AToB = 0.035611, Trd_of_AToB = 0.908194, Num_of_AToB = 9.0
Inh_of_CToB = 0.038629, Trd_of_CToB = 0.242677, Num_of_CToB = 7.0
Inh_of_DToB = 0.077111, Trd_of_DToB = 0.452594, Num_of_DToB = 10.0
Inh_of_AToC = 0.012452, Trd_of_AToC = 0.074465, Num_of_AToC = 10.0
Inh_of_BToC = 0.013795, Trd_of_BToC = 1.201145, Num_of_BToC = 7.0
Inh_of_DToC = 0.015959, Trd_of_DToC = 0.457424, Num_of_DToC = 9.0
Inh_of_AToD = 0.011011, Trd_of_AToD = 0.246773, Num_of_AToD = 6.0
Inh_of_BToD = 0.010941, Trd_of_BToD = 1.061017, Num_of_BToD = 9.0
Inh_of_CToD = 0.088197, Trd_of_CToD = 1.212272, Num_of_CToD = 10.0
Inh_of_BToA = 0.086486, Trd_of_BToA = 0.180382, Num_of_BToA = 7.0
Inh_o

KeyboardInterrupt: 

In [14]:
# ────────────────────────────────────────────────────────────────────────────────
# 5) Loop & write RACIPE‐style output, flushing after each line
# ────────────────────────────────────────────────────────────────────────────────

out =  "sim_test_output.dat"
with open(out, 'w') as fout:
    for idx in trange(len(pars), desc="Param sets"):
        row = pars.iloc[idx]
        s_no = int(row["S_no"])
        ss   = find_steady_states(row)           # 7 sets × 10 ICs × 200 steps
        line = [s_no, len(ss)]
        for st in ss:
            line += st.tolist()
        fout.write("\t".join(f"{v:.6g}" for v in line) + "\n")
        fout.flush()

Param sets:  50%|█████     | 1/2 [00:37<00:37, 37.54s/it]


KeyboardInterrupt: 

In [ ]:

# ────────────────────────────────────────────────────────────────────────────────
# 1) Load parameter names and parameter file (first 100 rows for testing)
# ────────────────────────────────────────────────────────────────────────────────
pt = "/Users/hiteshkandarpa/Desktop/IISC/Summer'25/Code/initial_sims/Toggle_tetrahedron/Hypothesis_test"
params_file = os.path.join(pt, "TS_parameters.dat")
names_file  = os.path.join(pt, "TS.prs")

# Read TTr.prs, ignore first header line, take only the first token each line
with open(names_file, 'r') as f:
    lines       = [ln.strip() for ln in f if ln.strip()]
param_names = [ln.split()[0] for ln in lines[1:]]

# Read parameters: col0=S_no, col1=Reported_states, cols2+ = kinetic values
pars = pd.read_csv(
    params_file,
    delim_whitespace=True,
    header=None,
    names=["S_no", "Reported_states"] + param_names,
    nrows=10
)

# Extract gene list ['A','B','C','D'] from "Prod_of_<Gene>"
genes = ['A','B','C','D']
ng   = len(genes)
gene_index = {g:i for i,g in enumerate(genes)}

# ────────────────────────────────────────────────────────────────────────────────
# 2) Precompute parameter‐arrays (Prod, Deg, lam, K, n) for one row
# ────────────────────────────────────────────────────────────────────────────────
def extract_param_arrays(row):
    p = row[param_names]
    # production & degradation vectors
    Prod = p[[f"Prod_of_{G}" for G in genes]].values.astype(float)
    Deg  = p[[f"Deg_of_{G}"  for G in genes]].values.astype(float)
    
    # initialize matrices
    lam = np.zeros((ng,ng), float)
    K   = np.zeros((ng,ng), float)
    nco = np.zeros((ng,ng), float)
    for H in genes:
        for G in genes:
            print(f'Prod_of_{G}={Prod},\n deg_of_{G}={Deg}')
            if H == G:
                continue
            i, j = gene_index[H], gene_index[G]
            lam[i,j] = float(p[f"Inh_of_{H}To{G}"])
            K[i,j]   = float(p[f"Trd_of_{H}To{G}"])
            nco[i,j] = float(p[f"Num_of_{H}To{G}"])
            print(f'Inh_of_{H}To{G} = {lam[i,j]}, Trd_of_{H}To{G} = {K[i,j]}, Num_of_{H}To{G} = {nco[i,j]}')

    # print(f'Prod={Prod},\n deg={Deg}, \n lam={lam}, \n threshold={K}, \n n={nco}')
    return Prod, Deg, lam, K, nco

# ────────────────────────────────────────────────────────────────────────────────
# 3) Vectorized RHS for all ICs at once
# ────────────────────────────────────────────────────────────────────────────────
def ode_rhs_vector(Xs, Prod, Deg, lam, K, nco):
    """
    Xs: shape (n_ics, ng)
    Prod,Deg: shape (ng,)
    lam,K,nco: shape (ng,ng), lam[ii]=0, no self-reg
    returns dXs shape (n_ics, ng)
    """
    # compute Xs^n per edge: shape (n_ics, ng, ng)
        # new Hill: 1 / (1 + (X/K)^n)
    ratio  = Xs[:,:,None] / K[None,:,:]
    print(K)           # shape (n_ics, ng, ng)
    hill   = 1.0 / (1.0 + ratio**(nco[None,:,:]))  # shape (n_ics, ng, ng)
    # shifted‐Hill factors: (1-lam)*hill+lam
    factors = (1 - lam)[None,:,:]* hill + lam[None,:,:] 
    # product over regulators axis=1 → shape (n_ics, ng)
    prod    = Prod[None,:] * np.prod(factors, axis=1)
    dXs     = prod - Deg[None,:] * Xs
    return dXs

# ────────────────────────────────────────────────────────────────────────────────
# 4) Vectorized Euler integrator
# ────────────────────────────────────────────────────────────────────────────────
def integrate_euler_vectorized(Prod, Deg, lam, K, nco,
                               n_ics=100, dt=0.1, n_steps=20000):
    # initial conditions: (Prod/Deg)*rand
    Xs = np.random.rand(n_ics, ng) * (Prod[None,:] / Deg[None,:])
    for _ in range(n_steps):
        dXs = ode_rhs_vector(Xs, Prod, Deg, lam, K, nco)
        Xs  = Xs + dt * dXs
        Xs[Xs<0] = 0
    return Xs  # shape (n_ics, ng)

# ────────────────────────────────────────────────────────────────────────────────
# 5) Find unique steady‐states by clustering final rows
# ────────────────────────────────────────────────────────────────────────────────
def find_steady_states_vectorized(row,
                                  n_ics=100,
                                  dt=0.1,
                                  n_steps=20000,
                                  tol_cluster=1.0):
    Prod, Deg, lam, K, nco = extract_param_arrays(row)
    Xs = integrate_euler_vectorized(Prod, Deg, lam, K, nco,
                                     n_ics=n_ics, dt=dt, n_steps=n_steps)
    finals = []
    for xf in Xs:
        if not any(np.allclose(xf, f, atol=tol_cluster) for f in finals):
            finals.append(xf)
    return finals

# ────────────────────────────────────────────────────────────────────────────────
# 6) Simulate all parameter sets and write RACIPE‐style output
# ────────────────────────────────────────────────────────────────────────────────
output_file = os.path.join(pt, "simulated_steady_states_vectorized.dat")
with open(output_file, 'w') as fout:
    for idx in trange(len(pars), desc="Vectorized sim"):
        row = pars.iloc[idx]
        s_no = int(row["S_no"])
        ss   = find_steady_states_vectorized(row,
                                              n_ics=100,
                                              dt=0.1,
                                              n_steps=20000,
                                              tol_cluster=1.0)
        line = [s_no, len(ss)] + [np.log2(val) if val>0 else -np.inf for st in ss for val in st.tolist()]
        fout.write("\t".join(f"{v:.6g}" for v in line) + "\n")


# Use this only 

In [35]:
import os
import pandas as pd
import numpy as np
from collections import Counter
from tqdm import trange

# 1) Load parameter names and parameter file (first 100 rows for testing)
pt = "/Users/hiteshkandarpa/Desktop/IISC/Summer'25/Code/initial_sims/Toggle_tetrahedron/Hypothesis_test"
params_file = os.path.join(pt, "TS_parameters.dat")
names_file  = os.path.join(pt, "TS.prs")

# Read TS.prs, ignore first header line, take only the first token each line
with open(names_file, 'r') as f:
    lines       = [ln.strip() for ln in f if ln.strip()]
param_names = [ln.split()[0] for ln in lines[1:]]

# Read parameters: col0=S_no, col1=Reported_states, cols2+ = kinetic values
pars = pd.read_csv(
    params_file,
    delim_whitespace=True,
    header=None,
    names=["S_no", "Reported_states"] + param_names,
    nrows=10
)

# Extract gene list ['A','B','C','D'] from "Prod_of_<Gene>"
genes = ['A', 'B', 'C', 'D']
ng   = len(genes)
gene_index = {g:i for i, g in enumerate(genes)}

# 2) Precompute parameter‐arrays (Prod, Deg, lam, K, n) for one row
def extract_param_arrays(row):
    p = row[param_names]
    Prod = p[[f"Prod_of_{G}" for G in genes]].astype(float).values
    Deg  = p[[f"Deg_of_{G}"  for G in genes]].astype(float).values
    lam = np.zeros((ng,ng))
    K   = np.zeros((ng,ng))
    nco = np.zeros((ng,ng))
    np.fill_diagonal(K, 1.0)
    np.fill_diagonal(nco, 0.0)
    for H in genes:
        for G in genes:
            if H == G:
                continue
            i, j = gene_index[H], gene_index[G]
            lam[i,j] = float(p[f"Inh_of_{H}To{G}"])
            K[i,j]   = float(p[f"Trd_of_{H}To{G}"])
            nco[i,j] = float(p[f"Num_of_{H}To{G}"])
    return Prod, Deg, lam, K, nco

# 3) Vectorized RHS for all ICs at once
def ode_rhs_vector(Xs, Prod, Deg, lam, K, nco):
    ratio = Xs[:,:,None] / K[None,:,:]
    # print(K)  # shape (n_ics, ng, ng)
    hill  = 1.0 / (1.0 + ratio**(nco[None,:,:]))
    factors = (1 - lam)[None,:,:] * hill + lam[None,:,:]
    prod    = Prod[None,:] * np.prod(factors, axis=1)
    dXs     = prod - Deg[None,:] * Xs
    return dXs

# 4) Vectorized Euler integrator
def integrate_euler_vectorized(Prod, Deg, lam, K, nco,
                               n_ics=100, dt=0.1, n_steps=20000):
    """
    Xs initial conditions: each X0_{i,G} ~ Uniform(0, Prod[G]/Deg[G])
    """
    # uniform on [0,1), then scale by Prod/Deg
    scale = (Prod[None, :] / Deg[None, :])  # shape (1, ng)
    Xs = np.random.uniform(0, 1, size=(n_ics, ng)) * scale

    for _ in range(n_steps):
        Xs += dt * ode_rhs_vector(Xs, Prod, Deg, lam, K, nco)
        Xs[Xs < 0] = 0
    return Xs


# 5) Find unique steady‐states by clustering final rows
def find_steady_states_vectorized(row,
                                  n_ics=100,
                                  dt=0.1,
                                  n_steps=20000,
                                  tol_cluster=1.0):
    Prod, Deg, lam, K, nco = extract_param_arrays(row)
    Xs = integrate_euler_vectorized(Prod, Deg, lam, K, nco,
                                     n_ics=n_ics, dt=dt, n_steps=n_steps)
    finals = []
    for xf in Xs:
        if not any(np.allclose(xf, f, atol=tol_cluster) for f in finals):
            finals.append(xf)
    return finals

# 6) Simulate all parameter sets and write RACIPE‐style output
output_file = os.path.join(pt, "simulated_steady_states_vectorized.dat")
with open(output_file, 'w') as fout:
    for idx in trange(len(pars), desc="Vectorized sim"):
        row = pars.iloc[idx]
        prodA = float(row["Prod_of_A"])      
        # Use the exact S_no from the parameter file
        s_no = int(row["S_no"])
        ss   = find_steady_states_vectorized(row,
                                              n_ics=100,
                                              dt=0.1,
                                              n_steps=20000,
                                              tol_cluster=1.0)
        # Log2 transform, handle non-positive
        flattened = [np.log2(v) if v>0 else -np.inf for st in ss for v in st]
        # Compose line: [S_no, number of states, log2 steady‐states...]
        line = [s_no, prodA, len(ss)] + flattened
        fout.write("\t".join(f"{x:.6g}" for x in line) + "\n")



/var/folders/6q/3gs9cqgs6ll9y2vljypxl7n80000gn/T/ipykernel_5232/1415883912.py:18: FutureWarning: The 'delim_whitespace' keyword in pd.read_csv is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  pars = pd.read_csv(
Vectorized sim: 100%|██████████| 10/10 [00:07<00:00,  1.36it/s]


# SymPy vetting

In [5]:
import sympy as sp

# 1) Declare symbols for genes
A, B, C, D = sp.symbols('A B C D')
genes = [A, B, C, D]

# 2) Declare symbols for all your parameters
#    (example names—replace with your full param_names list)
gA, gB, gC, gD = sp.symbols('Prod_of_A Prod_of_B Prod_of_C Prod_of_D')
dA, dB, dC, dD = sp.symbols('Deg_of_A Deg_of_B Deg_of_C Deg_of_D')
# inhibition params:
lamBA, KBA, nBA = sp.symbols('Inh_of_BToA Trd_of_BToA Num_of_BToA')
lamCA, KCA, nCA = sp.symbols('Inh_of_CToA Trd_of_CToA Num_of_CToA')
lamDA, KDA, nDA = sp.symbols('Inh_of_DToA Trd_of_DToA Num_of_DToA')

lamAB, KAB, nAB = sp.symbols('Inh_of_AToB Trd_of_AToB Num_of_AToB')
lamCB, KCB, nCB = sp.symbols('Inh_of_CToB Trd_of_CToB Num_of_CToB')
lamDB, KDB, nDB = sp.symbols('Inh_of_DToB Trd_of_DToB Num_of_DToB')

lamAC, KAC, nAC = sp.symbols('Inh_of_AToC Trd_of_AToC Num_of_AToC')
lamBC, KBC, nBC = sp.symbols('Inh_of_BToC Trd_of_BToC Num_of_BToC')
lamDC, KDC, nDC = sp.symbols('Inh_of_DToC Trd_of_DToC Num_of_DToC')

lamAD, KAD, nAD = sp.symbols('Inh_of_AToD Trd_of_AToD Num_of_AToD')
lamBD, KBD, nBD = sp.symbols('Inh_of_BToD Trd_of_BToD Num_of_BToD')
lamCD, KCD, nCD = sp.symbols('Inh_of_CToD Trd_of_CToD Num_of_CToD')

# … repeat for all 12 edges …

# 3) Build each dX/dt using the shifted‐Hill 1/(1+(X/K)**n) form
def shifted_inh(H, lam, K, n):
    hill = 1/(1 + (H/K)**n)
    return (1 - lam)*hill + lam

# dA/dt
exprA = gA \
    * shifted_inh(B, lamBA, KBA, nBA) \
    * shifted_inh(C, lamCA, KCA, nCA) \
    * shifted_inh(D, lamDA, KDA, nDA) \
    - dA*A

# Similarly for dB, dC, dD:
exprB = gB \
    * shifted_inh(A, lamAB, KAB, nAB) \
    * shifted_inh(C, lamCB, KCB, nCB) \
    * shifted_inh(D, lamDB, KDB, nDB) \
    - dB*B

exprC = gC \
    * shifted_inh(A, lamAC, KAC, nAC) \
    * shifted_inh(B, lamBC, KBC, nBC) \
    * shifted_inh(D, lamDC, KDC, nDC) \
    - dC*C

exprD = gD \
    * shifted_inh(A, lamAD, KAD, nAD) \
    * shifted_inh(B, lamBD, KBD, nBD) \
    * shifted_inh(C, lamCD, KCD, nCD) \
    - dD*D

# 4) Pack into a list
odes = [exprA, exprB, exprC, exprD]
params = [gA,gB,gC,gD, dA,dB,dC,dD,
          lamBA,KBA,nBA, lamCA,KCA,nCA, lamDA,KDA,nDA,
          lamAB,KAB,nAB, lamCB,KCB,nCB, lamDB,KDB,nDB,
          lamAC,KAC,nAC, lamBC,KBC,nBC, lamDC,KDC,nDC,
          lamAD,KAD,nAD, lamBD,KBD,nBD, lamCD,KCD,nCD]

# 5) Optional: simplify
odes_simpl = [sp.simplify(e) for e in odes]

In [6]:
for equation in odes_simpl:
    display(Math(sp.latex(equation)))

<IPython.core.display.Math object>

<IPython.core.display.Math object>

<IPython.core.display.Math object>

<IPython.core.display.Math object>

In [3]:

# 1) Load parameter names and first 10 rows of the parameter file
pt = "/Users/hiteshkandarpa/Desktop/IISC/Summer'25/Code/initial_sims/Toggle_tetrahedron/Hypothesis_test"
params_file = os.path.join(pt, "TS_parameters.dat")
names_file  = os.path.join(pt, "TS.prs")

# Read TS.prs, ignore header, get only name tokens
with open(names_file, 'r') as f:
    lines       = [ln.strip() for ln in f if ln.strip()]
param_names = [ln.split()[0] for ln in lines[1:]]

# Read only the first 10 parameter sets
pars = pd.read_csv(
    params_file,
    delim_whitespace=True,
    header=None,
    names=["S_no", "Reported_states"] + param_names,
    nrows=10
)

# Gene list
genes = ['A','B','C','D']
ng = len(genes)
gene_index = {g:i for i,g in enumerate(genes)}

# 2) Extract parameter arrays for one row
def extract_param_arrays(row):
    p = row[param_names]
    Prod = p[[f"Prod_of_{G}" for G in genes]].astype(float).values
    Deg  = p[[f"Deg_of_{G}"  for G in genes]].astype(float).values
    lam = np.zeros((ng,ng))
    K   = np.zeros((ng,ng))
    nco = np.zeros((ng,ng))
    np.fill_diagonal(K, 1.0)
    np.fill_diagonal(nco, 0.0)
    for H in genes:
        for G in genes:
            if H == G: continue
            i,j = gene_index[H], gene_index[G]
            lam[i,j] = float(p[f"Inh_of_{H}To{G}"])
            K[i,j]   = float(p[f"Trd_of_{H}To{G}"])
            nco[i,j] = float(p[f"Num_of_{H}To{G}"])
    return Prod, Deg, lam, K, nco

# 3) RHS for vectorized Euler
def ode_rhs_vector(Xs, Prod, Deg, lam, K, nco):
    ratio = Xs[:,:,None] / K[None,:,:]
    hill  = 1.0 / (1.0 + ratio**(nco[None,:,:]))
    factors = (1 - lam)[None,:,:] + lam[None,:,:] * hill
    prod    = Prod[None,:] * np.prod(factors, axis=1)
    return prod - Deg[None,:] * Xs

# 4) Euler integrator
def integrate_euler_vectorized(Prod, Deg, lam, K, nco,
                               n_ics=100, dt=0.1, n_steps=20000):
    scale = (Prod[None,:] / Deg[None,:])
    Xs = np.random.uniform(0, 1, size=(n_ics, ng)) * scale
    for _ in range(n_steps):
        Xs += dt * ode_rhs_vector(Xs, Prod, Deg, lam, K, nco)
        Xs[Xs < 0] = 0
    return Xs

# 5) Find unique steady states
def find_steady_states(row, n_ics=100, dt=0.1, n_steps=20000, tol=1.0):
    Prod, Deg, lam, K, nco = extract_param_arrays(row)
    Xs = integrate_euler_vectorized(Prod, Deg, lam, K, nco,
                                     n_ics=n_ics, dt=dt, n_steps=n_steps)
    finals = []
    for xf in Xs:
        if not any(np.allclose(xf, f, atol=tol) for f in finals):
            finals.append(xf)
    return finals

# 6) Run and collect results
results = []
for idx in trange(len(pars), desc="Simulating 10 sets"):
    row = pars.iloc[idx]
    s_no = int(row["S_no"])
    ss   = find_steady_states(row, n_ics=100, dt=0.1, n_steps=20000, tol=1.0)
    flattened = [np.log2(v) if v>0 else -np.inf for st in ss for v in st]
    results.append([s_no, len(ss)] + flattened)

# Display as DataFrame
cols = ["S_no", "n_states"] + [f"{g}_ss{i//4+1}" for i,g in enumerate(genes*max(len(r)-2 for r in results))]
df_out = pd.DataFrame(results, columns=cols[:len(results[0])])
df_out


/var/folders/6q/3gs9cqgs6ll9y2vljypxl7n80000gn/T/ipykernel_45953/3001425301.py:12: FutureWarning: The 'delim_whitespace' keyword in pd.read_csv is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  pars = pd.read_csv(
Simulating 10 sets: 100%|██████████| 10/10 [00:06<00:00,  1.49it/s]


S_no  n_states     A_ss1     B_ss1     C_ss1     D_ss1
0     1         1  8.385343  6.623968  5.573389  6.813134
1     2         1  4.169720  5.383644  6.968651  2.743373
2     3         1  5.677325  4.765576  6.850776  6.532066
3     4         1  7.270536  6.090269  3.357148  3.763138
4     5         1  4.687853  7.478303  4.835952  7.387798
5     6         1  5.688033  6.491501  5.259305  4.435010
6     7         1  6.850624  7.328429  7.028534  6.897493
7     8         1  6.742222  7.248073  6.708972  8.626413
8     9         1  6.176338  4.477168  7.463000  7.226913
9    10         1  3.733811  8.576053  7.542402  6.442589

In [42]:
print("Sympy‐Euler final:", trajectory[-1])

Sympy‐Euler final: [94.9764541  47.34013382 21.02987949 89.07033792]


# Lambdafying this shit 

In [69]:

# ────────────────────────────────────────────────────────────────────────────────
# B) Lambdify for numerical use
# ────────────────────────────────────────────────────────────────────────────────
f_num = sp.lambdify(
    (A, B, C, D) + tuple(params),
    odes_simpl,
    'numpy'
)

# ────────────────────────────────────────────────────────────────────────────────
# C) Numeric simulation to verify (first 10 parameter sets)
# ────────────────────────────────────────────────────────────────────────────────
# Load first 10 rows of TS_parameters.dat
pt = "/Users/hiteshkandarpa/Desktop/IISC/Summer'25/Code/initial_sims/Toggle_tetrahedron/Hypothesis_test"
names_file  = os.path.join(pt, "TS.prs")
with open(names_file, 'r') as f:
    lines = [ln.strip() for ln in f if ln.strip()]
param_names = [ln.split()[0] for ln in lines[1:]]
pars = pd.read_csv(
    os.path.join(pt, "TS_parameters.dat"),
    sep=r'\s+',
    header=None,
    names=["S_no","Reported_states"] + param_names,
    nrows=5
)

dt = 0.1
n_steps = 20000
tol = 1.0
n_ics = 100

results = []
for idx in trange(len(pars), desc="Sympy‐verified sim"):
    row = pars.iloc[idx]
    s_no = int(row["S_no"])
    param_vals = [float(row[str(p)]) for p in params]
    finals = []
    for _ in range(n_ics):
        # uniform IC on [0, Prod/Deg]
        X = np.array([row[f"Prod_of_{G}"]/row[f"Deg_of_{G}"] * np.random.uniform(0,1) for G in ['A','B','C','D']])
        for _ in range(n_steps):
            dX = np.array(f_num(*X, *param_vals), float)
            X += dt*dX
            X[X<0] = 0
        if not any(np.allclose(X, F, atol=tol) for F in finals):
            finals.append(X.copy())
    flat = [np.log2(v) if v>0 else -np.inf for state in finals for v in state]
    results.append([s_no, len(finals)] + flat)

max_states = max((len(r) - 2)//4 for r in results)

# build column names
cols = ["S_no","n_states"] + [
    f"{g}_ss{s+1}"
    for s in range(max_states)
    for g in genes
]

# create the DataFrame — pandas will fill missing cells with NaN for rows
# that have fewer than max_states
df_verify = pd.DataFrame(results, columns=cols)

df_verify

Sympy‐verified sim: 100%|██████████| 5/5 [00:59<00:00, 11.87s/it]


S_no  n_states     A_ss1     B_ss1     C_ss1     D_ss1     A_ss2     B_ss2  \
0     1         2  0.549570 -1.211174 -6.659352  0.475810  5.106405  2.037353   
1     2         1 -7.318248  0.707534  2.100855 -2.847394       NaN       NaN   
2     3         2 -3.927558 -7.955583  1.964067 -0.047971  1.610899 -2.782800   
3     4         1  0.766111 -0.029790 -7.851651 -6.870361       NaN       NaN   
4     5         3 -6.973290  1.944064 -4.252845  0.911907 -7.595038  4.546211   

      C_ss2     D_ss2     A_ss3     B_ss3     C_ss3     D_ss3  
0 -6.853657 -6.040165       NaN       NaN       NaN       NaN  
1       NaN       NaN       NaN       NaN       NaN       NaN  
2  0.334529 -5.695817       NaN       NaN       NaN       NaN  
3       NaN       NaN       NaN       NaN       NaN       NaN  
4 -0.031973 -4.260922 -7.537327 -1.214237  0.032266  1.998035

# Vectorised Sympy Lambdified code 

In [7]:
# ────────────────────────────────────────────────────────────────────────────────
# B) Lambdify for numerical use
# ────────────────────────────────────────────────────────────────────────────────
f_num = sp.lambdify(
    (A, B, C, D) + tuple(params),
    odes_simpl,
    'numpy'
)

# ────────────────────────────────────────────────────────────────────────────────
# C) Numeric simulation to verify (first 10 parameter sets)
# ────────────────────────────────────────────────────────────────────────────────
# Load first 10 rows of TS_parameters.dat
pt = "/Users/hiteshkandarpa/Desktop/IISC/Summer'25/Code/initial_sims/Toggle_tetrahedron/Hypothesis_test"
names_file  = os.path.join(pt, "TS.prs")
with open(names_file, 'r') as f:
    lines = [ln.strip() for ln in f if ln.strip()]
param_names = [ln.split()[0] for ln in lines[1:]]
pars = pd.read_csv(
    os.path.join(pt, "TS_parameters.dat"),
    sep=r'\s+',
    header=None,
    names=["S_no","Reported_states"] + param_names,
    nrows=50
)
# ────────────────────────────────────────────────────────────────────────────────
# 3) Vectorized Euler using f_num
# ────────────────────────────────────────────────────────────────────────────────
def integrate_euler_sympy(row, n_ics=100, dt=0.1, n_steps=20000):
    # extract numeric params in correct order
    pvals = [float(row[str(p)]) for p in params]
    # scale for uniform IC
    scale = np.array([row[f"Prod_of_{G}"]/row[f"Deg_of_{G}"] for G in ['A','B','C','D']], float)
    Xs = np.random.uniform(0, 1, size=(n_ics, 4)) * scale[None,:]
    for _ in range(n_steps):
        A_vec, B_vec, C_vec, D_vec = Xs.T
        dA, dB, dC, dD = f_num(A_vec, B_vec, C_vec, D_vec, *pvals)
        Xs += dt * np.vstack((dA, dB, dC, dD)).T
        Xs[Xs<0] = 0
    return Xs

# ────────────────────────────────────────────────────────────────────────────────
# 4) Find unique steady states and collect
# ────────────────────────────────────────────────────────────────────────────────
results = []
tol = 1.0
for idx in trange(len(pars), desc="Sympy‐vectorized sim"):
    row = pars.iloc[idx]
    s_no = int(row["S_no"])
    Xs = integrate_euler_sympy(row)  # shape (100,4)
    finals = []
    for x in Xs:
        if not any(np.allclose(x, f, atol=tol) for f in finals):
            finals.append(x.copy())
    flat = [np.log2(v) if v>0 else -np.inf for state in finals for v in state]
    results.append([s_no, len(finals)] + flat)

# ────────────────────────────────────────────────────────────────────────────────
# 5) Assemble DataFrame
# ────────────────────────────────────────────────────────────────────────────────
genes = ['A','B','C','D']
max_states = max((len(r)-2)//4 for r in results)
cols = ["S_no","n_states"] + [f"{g}_ss{s+1}" for s in range(max_states) for g in genes]
df_verify = pd.DataFrame(results, columns=cols)

df_verify


Sympy‐vectorized sim: 100%|██████████| 50/50 [00:56<00:00,  1.12s/it]


S_no  n_states      A_ss1      B_ss1     C_ss1     D_ss1      A_ss2  \
0      1         2   5.106405   2.037353 -6.853657 -6.040165   0.549570   
1      2         1  -7.318248   0.707534  2.100855 -2.847394        NaN   
2      3         2   1.610899  -2.782800  0.334529 -5.695817  -3.927558   
3      4         3   0.766111  -0.029790 -7.851651 -6.870361  -5.809076   
4      5         3  -6.973290   1.944064 -4.252845  0.911907  -7.537327   
5      6        20  -1.415188   4.243643 -7.024047 -0.058239  -0.241902   
6      7         1  -1.595041   0.900125  1.618447 -8.546425        NaN   
7      8         2   0.555849  -1.424328 -5.000178  2.399917  -4.678974   
8      9         2  -4.418381  -7.285463  6.066426  3.792055  -0.405660   
9     10         1  -3.459029   2.930963  1.128937 -5.255404        NaN   
10    11         2  -5.505420  -6.741346  0.233302  1.575159  -1.014937   
11    12         2   2.304632  -2.353877 -3.161199  3.521874  -3.647988   
12    13         2   2.002925   1.938302 -4.293819 -7.673988   2.867184   
13    14         2   1.652020  -5.144553 -3.152587  1.497644   2.113621   
14    15         3   0.528843  -1.785551  1.014589 -9.753104  -2.814884   
15    16         1 -10.575940   3.263790 -7.956661  4.314014        NaN   
16    17         2  -6.041537  -7.769292  2.450421  3.690910  -0.265656   
17    18         2  -6.812222  -0.949605 -0.202878  2.866587   1.377913   
18    19         2  -3.415031   3.487703  1.038205 -5.487643   1.284868   
19    20         1   0.961305  -6.415885 -6.173493  4.230860        NaN   
20    21         5  -1.440882  -0.342486  6.244117 -7.111145  -8.798475   
21    22         2   0.683525  -5.402795 -3.503126  5.187017  -3.641739   
22    23         2   0.767251   5.190038 -7.245411 -2.966622  -5.566957   
23    24         1  -5.225208   1.336940  2.798654 -3.981646        NaN   
24    25         2   2.520339  -5.351220  0.699306 -8.146453  -0.417991   
25    26         2   3.292187   2.222896 -7.699904 -6.131287   5.601722   
26    27         1  -6.715521  -6.271669  1.238425  2.191547        NaN   
27    28         3  -6.338960   3.513857  2.061539 -4.112294  -6.607482   
28    29         1  -2.316827  -0.870154  4.899386 -2.349714        NaN   
29    30         2  -3.802912   6.086649 -0.129384 -9.771113 -10.172728   
30    31         1   0.755169  -5.688306  6.441563 -6.485208        NaN   
31    32         2  -7.873642  -4.338626  1.305607  2.075998  -8.899357   
32    33         3  -6.795704   1.379778 -5.084324  1.852576  -3.106418   
33    34         1  -5.485948  -5.392578  2.790639  3.533024        NaN   
34    35         2  -2.214305  -9.819129  2.783802  4.131366   1.348598   
35    36         2   2.282835   3.102058 -2.860451 -6.689843   4.989210   
36    37         6  -7.862274   1.407154  0.610640 -4.909509  -4.095480   
37    38         3  -5.218976 -10.139614  2.307226  1.486629   0.658794   
38    39         2   2.391719  -7.093153  5.325634 -3.433677  -1.658570   
39    40         2  -4.170427   1.032885  1.497012 -9.178669   1.783892   
40    41         3   3.760966  -4.143328 -6.585626  1.219648   1.619364   
41    42         2   1.891708  -3.090384  3.146666 -5.999275  -4.682868   
42    43         3   3.337925  -5.057182  3.752762 -3.991807   3.566970   
43    44         2  -7.133540   2.792573  1.028563 -3.360308  -7.096445   
44    45         1   3.395646  -0.982908 -0.765807 -2.151986        NaN   
45    46         3  -3.076619   3.473732 -5.383051  3.014240   1.520265   
46    47         2   2.431773  -4.153305 -3.822888  2.351574   1.667585   
47    48         1  -1.337507  -8.070250 -0.494287  5.165604        NaN   
48    49         1  -0.859732   2.453968  1.010780 -8.234366        NaN   
49    50         3  -2.623798   0.879043 -3.911519  1.824763   2.249247   

        B_ss2      C_ss2     D_ss2  ...   C_ss18    D_ss18    A_ss19  \
0   -1.211174  -6.659352  0.475810  ...      NaN       NaN       NaN   
1         NaN        NaN       NaN

# Measuring differences Between RACIPE Output and Vectorised Sympy RACIPE 

In [76]:

# Path to RACIPE solutions file
raci_path = "/Users/hiteshkandarpa/Desktop/IISC/Summer'25/Code/initial_sims/Toggle_tetrahedron/Hypothesis_test/combined_solutions2.dat"

# 1) Read just the first two columns: parameter set number and reported number of states
df_raci = pd.read_csv(
    raci_path,
    sep=r'\s+',
    header=None,
    usecols=[0, 1],
    names=['S_no', 'R_states']
)

# 2) Filter to only those parameter sets you simulated (in df_verify)
df_raci_sub = df_raci[df_raci['S_no'].isin(df_verify['S_no'])]

# 3) Merge with your simulated results
df_comp = df_raci_sub.merge(
    df_verify[['S_no', 'n_states']],
    on='S_no',
    how='inner'
)

# 4) Compare
df_comp['match'] = df_comp['R_states'] == df_comp['n_states']
n_total   = len(df_comp)
n_match   = df_comp['match'].sum()
n_diff    = n_total - n_match
diff_sets = df_comp.loc[~df_comp['match'], 'S_no'].tolist()

# 5) Print summary
print(f"Compared {n_total} parameter sets (only those you simulated).")
print(f"{n_match} agree on steady‐state count.")
print(f"{n_diff} differ: {diff_sets}")

# 6) Show comparison details
df_comp


Compared 44 parameter sets (only those you simulated).
23 agree on steady‐state count.
21 differ: [4, 8, 10, 11, 12, 14, 20, 22, 29, 31, 33, 34, 38, 39, 42, 43, 45, 46, 47, 49, 50]


S_no  R_states  n_states  match
0      2         1         1   True
1      4         3         2  False
2      5         3         3   True
3      8        17         2  False
4      9         2         2   True
5     10         3         1  False
6     11         3         2  False
7     12         4         2  False
8     13         2         2   True
9     14         4         2  False
10    15         3         3   True
11    16         1         1   True
12    17         2         2   True
13    18         2         2   True
14    19         2         2   True
15    20         2         1  False
16    22         4         3  False
17    23         2         2   True
18    24         2         2   True
19    25         2         2   True
20    26         2         2   True
21    27         1         1   True
22    28         3         3   True
23    29         2         1  False
24    30         2         2   True
25    31         2         1  False
26    32         2         2   True
27    33         4         2  False
28    34         2         1  False
29    35         3         3   True
30    36         2         2   True
31    38         3         2  False
32    39         3         2  False
33    40         2         2   True
34    41         3         3   True
35    42         3         2  False
36    43         3         2  False
37    44         2         2   True
38    45         2         1  False
39    46         3         2  False
40    47         3         1  False
41    48         1         1   True
42    49         2         1  False
43    50         4         3  False

In [8]:
# Filter out parameter sets with >10 steady states and write RACIPE‐style output

import os

# genes and DataFrame from above
genes = ['A','B','C','D']

# 1) Drop rows with more than 10 steady states
df_filtered = df_verify[df_verify['n_states'] <= 10].copy()

# 2) Write to file in RACIPE format
output_path = os.path.join(pt, "RACIPE_custom_ss_noepigenetic.dat")
with open(output_path, 'w') as fout:
    for _, row in df_filtered.iterrows():
        s_no     = int(row['S_no'])
        n_states = int(row['n_states'])
        # collect only the actual steady‐state columns
        vals = []
        for s in range(n_states):
            for g in genes:
                vals.append(row[f"{g}_ss{s+1}"])
        # compose and write line
        line = [s_no, n_states] + vals
        fout.write("\t".join(f"{v:.6g}" for v in line) + "\n")

print(f"Wrote {len(df_filtered)} parameter sets to {output_path}")


Wrote 49 parameter sets to /Users/hiteshkandarpa/Desktop/IISC/Summer'25/Code/initial_sims/Toggle_tetrahedron/Hypothesis_test/RACIPE_custom_ss_noepigenetic.dat


# Parellelised Vectorised RACIPE

In [9]:
from joblib import Parallel, delayed

# 1) Define a helper to process one parameter set
def process_param(row, tol=1.0, n_ics=100, dt=0.1, n_steps=20000):
    s_no = int(row["S_no"])
    # integrate all ICs vectorized
    Xs = integrate_euler_sympy(row, n_ics=n_ics, dt=dt, n_steps=n_steps)
    # cluster unique finals
    finals = []
    for x in Xs:
        if not any(np.allclose(x, f, atol=tol) for f in finals):
            finals.append(x.copy())
    # log2 transform
    flat = [np.log2(v) if v>0 else -np.inf for state in finals for v in state]
    return [s_no, len(finals)] + flat

# 2) Parallel execution over your pars DataFrame
#    Use all available cores; set n_jobs accordingly
results = Parallel(n_jobs=-1)(
    delayed(process_param)(pars.iloc[i])
    for i in range(len(pars))
)

# 3) Assemble into DataFrame
genes = ['A','B','C','D']
max_states = max((len(r) - 2)//4 for r in results)
cols = ["S_no","n_states"] + [
    f"{g}_ss{s+1}"
    for s in range(max_states)
    for g in genes
]
df_verify_parallel = pd.DataFrame(results, columns=cols)

df_verify_parallel


S_no  n_states      A_ss1      B_ss1     C_ss1     D_ss1      A_ss2  \
0      1         2   5.106405   2.037353 -6.853657 -6.040165   0.549570   
1      2         1  -7.318248   0.707534  2.100855 -2.847394        NaN   
2      3         2   1.610899  -2.782800  0.334529 -5.695817  -3.927558   
3      4         3   0.766111  -0.029790 -7.851651 -6.870361  -5.809076   
4      5         3  -6.973290   1.944064 -4.252845  0.911907  -7.595038   
5      6        20  -4.932436   1.351199 -6.533957  1.002542  -0.596814   
6      7         1  -1.595041   0.900125  1.618447 -8.546425        NaN   
7      8         3   0.555849  -1.424328 -5.000178  2.399917  -4.678974   
8      9         2  -4.418381  -7.285463  6.066426  3.792055  -0.405660   
9     10         1  -3.459029   2.930963  1.128937 -5.255404        NaN   
10    11         2  -5.505420  -6.741346  0.233302  1.575159  -1.014937   
11    12         2   2.304632  -2.353877 -3.161199  3.521874  -3.647988   
12    13         2   2.002925   1.938302 -4.293819 -7.673988   2.867184   
13    14         2   1.652020  -5.144553 -3.152587  1.497644   2.113621   
14    15         3   0.528843  -1.785551  1.014589 -9.753104  -2.814884   
15    16         1 -10.575940   3.263790 -7.956661  4.314014        NaN   
16    17         2  -6.041537  -7.769292  2.450421  3.690910  -0.265656   
17    18         2  -6.812222  -0.949605 -0.202878  2.866587   1.377913   
18    19         2  -3.415031   3.487703  1.038205 -5.487643   1.284868   
19    20         1   0.961305  -6.415885 -6.173493  4.230860        NaN   
20    21         3  -1.440882  -0.342486  6.244117 -7.111145   0.852572   
21    22         2   0.683525  -5.402795 -3.503126  5.187017  -3.641739   
22    23         2  -5.566957   5.584422 -7.029521  0.792394   0.767251   
23    24         1  -5.225208   1.336940  2.798654 -3.981646        NaN   
24    25         2   2.520339  -5.351220  0.699306 -8.146453  -0.417991   
25    26         2   3.292187   2.222896 -7.699904 -6.131287   5.601722   
26    27         1  -6.715521  -6.271669  1.238425  2.191547        NaN   
27    28         3  -5.759644  -1.651602  2.925274  1.101934  -6.607482   
28    29         2  -2.316827  -0.870154  4.899386 -2.349714  -5.978828   
29    30         2  -3.802912   6.086649 -0.129384 -9.771113 -10.172728   
30    31         1   0.755169  -5.688306  6.441563 -6.485208        NaN   
31    32         2  -7.873642  -4.338626  1.305607  2.075998  -8.899357   
32    33         2  -6.795704   1.379778 -5.084324  1.852576  -3.106418   
33    34         1  -5.485948  -5.392578  2.790639  3.533024        NaN   
34    35         2  -2.214305  -9.819129  2.783802  4.131366   3.864354   
35    36         2   2.282835   3.102058 -2.860451 -6.689843   4.989210   
36    37         8  -1.381280  -0.270561 -1.433498  1.214108  -0.600114   
37    38         2  -5.218976 -10.139614  2.307226  1.486629   0.658794   
38    39         2   2.391719  -7.093153  5.325634 -3.433677  -1.658570   
39    40         2   1.783892  -5.196662  1.638005 -9.199877  -4.170427   
40    41         2   3.760966  -4.143328 -6.585626  1.219648   1.619364   
41    42         2   1.891708  -3.090384  3.146666 -5.999275  -4.682868   
42    43         2   3.337925  -5.057182  3.752762 -3.991807   3.566970   
43    44         2  -7.133540   2.792573  1.028563 -3.360308  -7.096445   
44    45         1   3.395646  -0.982908 -0.765807 -2.151986        NaN   
45    46         2  -3.076619   3.473732 -5.383051  3.014240   1.520265   
46    47         1   2.431773  -4.153305 -3.822888  2.351574        NaN   
47    48         1  -1.337507  -8.070250 -0.494287  5.165604        NaN   
48    49         2  -0.859732   2.453968  1.010780 -8.234366   1.420872   
49    50         3   2.249247  -4.797851 -6.069703  3.589096  -2.623798   

        B_ss2      C_ss2      D_ss2  ...   C_ss18    D_ss18   A_ss19  \
0   -1.211174  -6.659352   0.475810  ...      NaN       NaN      NaN   
1         NaN        NaN        Na

# Writing this to output file

In [10]:
# Filter out parameter sets with >10 steady states and write RACIPE‐style output

# genes and DataFrame from above
genes = ['A','B','C','D']

# 1) Drop rows with more than 10 steady states
df_filtered = df_verify_parallel[df_verify_parallel['n_states'] <= 10].copy()

# 2) Write to file in RACIPE format
output_path = os.path.join(pt, "RACIPE_custom_ss_noepigenetic.dat")
with open(output_path, 'w') as fout:
    for _, row in df_filtered.iterrows():
        s_no     = int(row['S_no'])
        n_states = int(row['n_states'])
        # collect only the actual steady‐state columns
        vals = []
        for s in range(n_states):
            for g in genes:
                vals.append(row[f"{g}_ss{s+1}"])
        # compose and write line
        line = [s_no, n_states] + vals
        fout.write("\t".join(f"{v:.6g}" for v in line) + "\n")

print(f"Wrote {len(df_filtered)} parameter sets to {output_path}")


Wrote 49 parameter sets to /Users/hiteshkandarpa/Desktop/IISC/Summer'25/Code/initial_sims/Toggle_tetrahedron/Hypothesis_test/RACIPE_custom_ss_noepigenetic.dat
